## error_pos_plotter.ipynb

Jupyter notebook whose aim is to plot the position error for each individual electrode. Based on logs after ICP post-processing.

Author: Kieran Le Mouël

Date: 07/07/2025

In [19]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [20]:
path_NAS = "/home/klemouel/NAS_EMPENN/share/users/klemouel/Stage/"
path_proc = path_NAS + "post_processing/T1_65/pos_errors/"
path_CSV = path_NAS + "Correspondancies_ElectrodeDetection_Dataset.csv"

In [ ]:
corr = pd.read_csv(path_CSV) # Reading the CSV
database = [] # Initialize empty list that will contain the read logging data

In [1]:
electrodes = {
    1: "FP2", 2: "FPZ", 3: "FP1", 4: "AF7", 5: "AF3", 6: "AFZ", 7: "AF4", 8: "AF8", 9: "F8", 10: "F6",
    11: "F4", 12: "F2", 13: "FZ", 14: "F1", 15: "F3", 16: "F5", 17: "F7", 18: "FT9", 19: "FT7", 20: "FC5",
    21: "FC3", 22: "FC1", 23: "FCZ", 24: "FC2", 25: "FC4", 26: "FC6", 27: "FT8", 28: "FT10", 29: "T8", 30: "C6",
    31: "C4", 32: "C2", 33: "CZ", 34: "C1", 35: "C3", 36: "C5", 37: "T7", 38: "TP9", 39: "TP7", 40: "CP5",
    41: "CP3", 42: "CP1", 43: "CPZ", 44: "CP2", 45: "CP4", 46: "CP6", 47: "TP8", 48: "TP10", 49: "P8", 50: "P6",
    51: "P4", 52: "P2", 53: "PZ", 54: "P1", 55: "P3", 56: "P5", 57: "P7", 58: "PO7", 59: "PO3", 60: "POZ",
    61: "PO4", 62: "PO8", 63: "O2", 64: "OZ", 65: "O1"
} # Dictionnary to associate case number with electrode name

In [ ]:
def load_all_data(l: list[str]) -> None:
    """
    Function used to load all logging data into a list. Data loaded as a string.

    Keyword argument:

    l -- list of strings used to store loaded data
    """
    for i, row in corr.iterrows():
        if(row['Set'] == "test"):
            id = str(row['Id'])
            id = id.rjust(3,'0')

            with open(path_proc + id +"_err.txt", 'r') as f:
                data = f.read()
                l.append(data)

load_all_data(database)

In [ ]:
def get_err_values(data: str) -> list:
    """
    Function used to get float error values from loaded data string.

    Keyword argument:

    data -- loaded data string
    """
    tmp = data.split("\n")
    tmp.pop(-1)
    l = []
    for i in tmp:
        haha = i.split(" ")
        l.append(float(haha[1]))
    return l

In [ ]:
def get_values_dict(data: str) -> dict:
    """
    Function used to get dictionary matching case number with float error value.

    Keyword argument:

    data -- loaded data string
    """
    tmp = data.split("\n")
    tmp.pop(-1)
    d = {}
    for i in tmp:
        hehe = i.split(" ")
        d[float(hehe[0])] = float(hehe[1])
    return d

In [ ]:
def avg(li: list[float]) -> float:
    """
    Function used to get the average value of a list of numerical values

    Keyword argument:

    li -- list to average
    """
    res = 0
    for i in range(0, len(li)):
        res += li[i]
    return res/len(li)

In [ ]:
def count_average(l: list[str]) -> float:
    """
    Function used to get the overall average of a list of loaded data.

    Keyword argument:

    l -- list of loaded data strings
    """
    res = 0
    for data in l:
        res += avg(get_err_values(data))
    return res/len(l)

In [41]:
def smooth(scalars: list[float], weight: float) -> list[float]:
    """
    Smoothing function using the Exponential moving average.

    Keywords arguments:
    
    scalars -- list of floats to be smoothed

    weight -- float value that handles smoothing aggressiveness
    """
    last = scalars[0]
    smoothed = list()
    for point in scalars:
        smoothed_val = last * weight + (1-weight) * point
        smoothed.append(smoothed_val)
        last = smoothed_val
    return smoothed   

In [ ]:
l = [] # List of average error values
vals = [] # List of lists containing error values
def __main__():
    sorted_list = []
    for data in database:
        d = get_values_dict(data)
        sorted_list = sorted(d)
        tmp = []
        for i in sorted_list:
            tmp.append(d[i])
        l.append(avg(tmp))
        vals.append(tmp)
    # print(vals)
    
    # for m in range(0, len(sorted_list)):
    #     res = []
    #     for n in range(0, len(vals)):
    #         res.append(vals[n][m])
    #     l.append(res)
    # return None

__main__()

In [ ]:
# Plot average error values for the 19 test cases
fig, ax = plt.subplots(1,1,figsize=(10,10))
ax.plot(l)
ax.set_title("title")
ax.set_xlabel("test case")
ax.set_ylabel("mean pos error value")
ax.set_xticks(np.arange(0,19,1))
ax.set_yticks(np.arange(0,4,1))
# x = 0
# y = 0
# for i in range(0,65):
#     res = []
#     for j in range(0,len(l[i])):
#         res.append(l[i][j])
#     # p = smooth(res, 0.9)
    # x += 1
    # if (i+1)%5 == 0:
    #     x = 0
    # if x == 0:
    #     y += 1

In [ ]:
# Plot error values for each electrode for the 19 test cases
fig, ax = plt.subplots(1,1,figsize=(100,100))
x = 0
y = 0
for i in range(0,65):
    res = []
    for j in range(0,19):
        res.append(vals[j][i])
    p = smooth(res, 0.9)
    ax.plot(p)
    ax.annotate(xy=(18,p[-1]), text = electrodes[i+1])
    x += 1
    if (i+1)%5 == 0:
        x = 0
    if x == 0:
        y += 1